# Finanz- und Sozialpolitik, Sommersemester 2024

# Klausur 1. August 2024, 9-11 Uhr

## Allgemeines

- Sie haben 120 Minuten Zeit zum Bearbeiten der Klausur, und anschließend weitere 60
  Minuten zum Hochladen des Notebooks auf eCampus. Wir erwarten jedoch, dass keine
  technischen Probleme beim Hochladen auftreten und sind gern behilflich, wenn Sie
  Schwierigkeiten haben. 
- Sie können maximal 150 Punkte erreichen. Den Kurs können Sie nur bestehen, wenn Sie
  mindestens 75 Punkte **in der Klausur** erreichen. In dem Fall werden etwaige
  Extrapunkte aus dem Semester hinzugezählt.
- In der Klausur sind alle Hilfsmittel erlaubt, nur gemeinsames Arbeiten ist strikt
  verboten.
- Wir empfehlen Ihnen, sich **jetzt** eine Kopie der Originalklausur zu erstellen, falls
  Sie ausversehen Zellen löschen. Sie können natürlich auch jederzeit wieder die Version
  von eCampus bzw. der Website herunterladen.

## Bearbeitungshinweise

- Sie können nur eine einzige Datei hochladen, beantworten Sie deshalb alle Fragen in
  diesem Notebook.
- Bei allen Fragen geben wir Ihnen Code- und / oder Markdownzellen für Ihre Antworten
  vor.
  - Wenn nur eine Codezelle vorhanden ist, erwarten wir auch nur eine Berechnung oder
    Graphik als Antwort.
  - Wenn nur eine Markdownzelle vorhanden ist, erwarten wir nur eine verbale Antwort.
  - Wenn beide Arten von Zellen vorhanden sind, erwarten wir sowohl eine Berechnung oder
    Graphik als auch eine verbale Antwort.
- Um Ihre Lösung nachzuvollziehen, ist es wichtig, dass in der abgegebenen Version die
  ausgeführten Zellen fortlaufend von 1 bis N nummeriert sind. **Vor der Abgabe lassen
  Sie daher bitte die bearbeitete Klausur per "Kernel" -> "Restart Kernel and Run all
  Cells" durchlaufen und speichern Sie das Notebook anschließend.**

## Abgabe und Rücktritt

- Wenn Sie nicht abgeben möchten, stellen Sie bitte sicher, dass keine Datei
  hochgeladen ist.

**Viel Erfolg!**

# Vorbemerkung

In der Klausur werden wir die Effekte von drei unterschiedlichen Reformen untersuchen. Die Reformen werden in Aufgaben 2, 3 und 4 näher beschrieben. Um Vergleiche anstellen zu können, untersuchen wir zunächst den Status quo. Um Verwirrung zu vermeiden, bezeichnen wir dementsprechend auch in Aufgabe 1 schon das DataFrame mit dem GETTSIM-Output `ergebnisse_personen_vor_reform`.

Es tauchen insgesamt drei Haushaltstypen in der Analyse auf. In den Haushalten mit zwei Erwachsenen erhält nur eine Person Lohn. Alle Aussagen über Steuern, Transfers und Arbeitsangebot beziehen sich auf den Fall, dass diese Person unterschiedliche Löhne bezieht. **Achtung: Dies ist in den Aufgabentexten lediglich  implizit, um die Beschreibungen knapp zu halten.** An keiner Stelle erwarten wir, dass Sie auf die Arbeitsanreize o.Ä. des nicht-arbeitenden Partners eingehen.

In [ ]:
from copy import deepcopy
from io import StringIO

import numpy as np
import pandas as pd

pd.options.plotting.backend = "plotly"

from gettsim import (
    compute_taxes_and_transfers,
    create_synthetic_data,
    set_up_policy_environment,
)

## Erstellung des Steuer- und Transfersystems

Wir setzen zunächst wieder die Parameter des Steuer- und Transfersystems auf die des
Jahres 2023.

In [ ]:
params_dict, policy_func_dict = set_up_policy_environment("2023-01-01")

## Generierung von Haushalten 

Wir erstellen 2 Typen von Haushalten:

- couple_0_children
- couple_0_children, 1 Kind

Die Haushalte werden wie im Kurs generiert, hier ist keine Überraschung eingebaut.

In [ ]:
min_einkommen = 0
max_einkommen = 10000
anzahl_schritte = 101

_bruttolohn_m = np.linspace(min_einkommen, max_einkommen, anzahl_schritte)

_df_1e_0k = create_synthetic_data(
    n_adults=1,
    n_children=0,
    specs_heterogeneous={
        "bruttolohn_m": [[i] for i in _bruttolohn_m],
    },
    policy_year=2023,
)
_df_2e_0k = create_synthetic_data(
    n_adults=2,
    n_children=0,
    specs_heterogeneous={
        "bruttolohn_m": [[i, 0] for i in _bruttolohn_m],
    },
    policy_year=2023,
)
_df_2e_2k = create_synthetic_data(
    n_adults=2,
    n_children=2,
    specs_heterogeneous={
        "bruttolohn_m": [[i, 0, 0, 0] for i in _bruttolohn_m],
    },
    policy_year=2023,
)
# IDs einzigartig machen
for i, df in enumerate([_df_1e_0k, _df_2e_0k, _df_2e_2k]):
    for _id in ["p_id", "hh_id", "tu_id"]:
        df[_id] += i * 1000

## Gewichte für verschiedene Haushaltstypen und Einkommen. 

Inspiriert aus dem Mikrozensus. Summieren sich zu eins. Ignorieren Sie diese Zelle.

In [ ]:
_gewichte = pd.read_csv(
    StringIO(
        'bruttolohn_m_hh,hh_typ,gewicht\n0.0,single_0_children,1.013822709295575e-05\n0.0,couple_0_children,7.17729708349524e-10\n0.0,"couple_2_children",1.4236674709329704e-11\n100.0,single_0_children,0.0007936422416424824\n100.0,couple_0_children,6.996364578857066e-07\n100.0,"couple_2_children",2.9757308069761222e-08\n200.0,single_0_children,0.005044312238807282\n200.0,couple_0_children,1.841865722157699e-05\n200.0,"couple_2_children",1.1768083661930498e-06\n300.0,single_0_children,0.012789902105196385\n300.0,couple_0_children,0.00012620510035053672\n300.0,"couple_2_children",1.06550943618819e-05\n400.0,single_0_children,0.021261101811155668\n400.0,couple_0_children,0.0004403442912316959\n400.0,"couple_2_children",4.571872908781503e-05\n500.0,single_0_children,0.028252962142167926\n500.0,couple_0_children,0.0010448533348360778\n500.0,"couple_2_children",0.0001273992878250776\n600.0,single_0_children,0.03291623194965662\n600.0,couple_0_children,0.0019483154852037554\n600.0,"couple_2_children",0.0002703777480442597\n700.0,single_0_children,0.03529427888759387\n700.0,couple_0_children,0.003093046530841668\n700.0,"couple_2_children",0.00047774825262680474\n800.0,single_0_children,0.03581438797844441\n800.0,couple_0_children,0.004386162865157536\n800.0,"couple_2_children",0.0007416731659729939\n900.0,single_0_children,0.03498704147285219\n900.0,couple_0_children,0.00572848280206163\n900.0,"couple_2_children",0.001047093736892957\n1000.0,single_0_children,0.033270612387129674\n1000.0,couple_0_children,0.007032940377456821\n1000.0,"couple_2_children",0.0013758891777474612\n1100.0,single_0_children,0.031027987558924344\n1100.0,couple_0_children,0.008232959111680474\n1100.0,"couple_2_children",0.0017101597677000248\n1200.0,single_0_children,0.02852560054399228\n1200.0,couple_0_children,0.009283953257332786\n1200.0,"couple_2_children",0.0020342914946372263\n1300.0,single_0_children,0.025948359240493497\n1300.0,couple_0_children,0.01016104751181478\n1300.0,"couple_2_children",0.0023359501672961503\n1400.0,single_0_children,0.023418036477349392\n1400.0,couple_0_children,0.010855214061746192\n1400.0,"couple_2_children",0.002606309725972393\n1500.0,single_0_children,0.021010057158026473\n1500.0,couple_0_children,0.011369141577083517\n1500.0,"couple_2_children",0.0028398114764885997\n1600.0,single_0_children,0.01876710856757964\n1600.0,couple_0_children,0.01171350621428416\n1600.0,"couple_2_children",0.0030336839094017927\n1700.0,single_0_children,0.016709499454454733\n1700.0,couple_0_children,0.011903911182737472\n1700.0,"couple_2_children",0.003187378534380707\n1800.0,single_0_children,0.014842738733812045\n1800.0,couple_0_children,0.011958536693423585\n1800.0,"couple_2_children",0.0033020157373795968\n1900.0,single_0_children,0.013162926171162811\n1900.0,couple_0_children,0.011896432585261898\n1900.0,"couple_2_children",0.0033798904330983328\n2000.0,single_0_children,0.011660500404319934\n2000.0,couple_0_children,0.011736343845431329\n2000.0,"couple_2_children",0.0034240583036009324\n2100.0,single_0_children,0.010322790345296\n2100.0,couple_0_children,0.011495953199567609\n2100.0,"couple_2_children",0.0034380059752882356\n2200.0,single_0_children,0.009135713283414533\n2200.0,couple_0_children,0.0111914359735216\n2200.0,"couple_2_children",0.003425399004475885\n2300.0,single_0_children,0.008084874603130348\n2300.0,couple_0_children,0.010837239842268585\n2300.0,"couple_2_children",0.003389897171977619\n2400.0,single_0_children,0.007156253999888986\n2400.0,couple_0_children,0.01044602032527861\n2400.0,"couple_2_children",0.003335025290086992\n2500.0,single_0_children,0.0063366100843234505\n2500.0,couple_0_children,0.010028679380410566\n2500.0,"couple_2_children",0.003264088134218557\n2600.0,single_0_children,0.00561369627451461\n2600.0,couple_0_children,0.009594468244140793\n2600.0,"couple_2_children",0.003180119358388546\n2700.0,single_0_children,0.004976352715328315\n2700.0,couple_0_children,0.009151126654782443\n2700.0,"couple_2_children",0.0030858558164039793\n2800.0,single_0_children,0.004414518888883794\n2800.0,couple_0_children,0.008705039050097051\n2800.0,"couple_2_children",0.0029837302942023907\n2900.0,single_0_children,0.0039191974093490175\n2900.0,couple_0_children,0.008261394662014141\n2900.0,"couple_2_children",0.002875877111676612\n3000.0,single_0_children,0.0034823895719459136\n3000.0,couple_0_children,0.007824343063819747\n3000.0,"couple_2_children",0.0027641463094268564\n3100.0,single_0_children,0.003097016326852525\n3100.0,couple_0_children,0.007397140042043911\n3100.0,"couple_2_children",0.0026501231816150844\n3200.0,single_0_children,0.0027568335859967036\n3200.0,couple_0_children,0.006982280987508585\n3200.0,"couple_2_children",0.002535150761181218\n3300.0,single_0_children,0.0024563475083250207\n3300.0,couple_0_children,0.006581620585189697\n3300.0,"couple_2_children",0.0024203535311436643\n3400.0,single_0_children,0.0021907331947176364\n3400.0,couple_0_children,0.006196478631165483\n3400.0,"couple_2_children",0.0023066611527173967\n3500.0,single_0_children,0.0019557587377589604\n3500.0,couple_0_children,0.00582773246945661\n3500.0,"couple_2_children",0.002194831394445648\n3600.0,single_0_children,0.0017477155893488969\n3600.0,couple_0_children,0.005475896935961044\n3600.0,"couple_2_children",0.002085471740867756\n3700.0,single_0_children,0.0015633555732226482\n3700.0,couple_0_children,0.005141192904818761\n3700.0,"couple_2_children",0.001979059375501049\n3800.0,single_0_children,0.0013998344699331707\n3800.0,couple_0_children,0.004823605615282208\n3800.0,"couple_2_children",0.0018759593886460628\n3900.0,single_0_children,0.0012546618622736815\n3900.0,couple_0_children,0.004522933958126402\n3900.0,"couple_2_children",0.0017764411699982491\n4000.0,single_0_children,0.0011256567964925623\n4000.0,couple_0_children,0.0042388318505819636\n4000.0,"couple_2_children",0.0016806930206487358\n4100.0,single_0_children,0.0010109087523988132\n4100.0,couple_0_children,0.003970842749146342\n4100.0,"couple_2_children",0.0015888350677198588\n4200.0,single_0_children,0.0009087433984993937\n4200.0,couple_0_children,0.00371842825499043\n4200.0,"couple_2_children",0.001500930594540088\n4300.0,single_0_children,0.0008176926195349492\n4300.0,couple_0_children,0.0034809916667826765\n4300.0,"couple_2_children",0.001416995915230213\n4400.0,single_0_children,0.0007364683316668824\n4400.0,couple_0_children,0.0032578972368505574\n4400.0,"couple_2_children",0.0013370089288751005\n4500.0,single_0_children,0.0006639396374030199\n4500.0,couple_0_children,0.0030484857925420217\n4500.0,"couple_2_children",0.0012609164881111964\n4600.0,single_0_children,0.0005991129131103995\n4600.0,couple_0_children,0.0028520872976230526\n4600.0,"couple_2_children",0.0011886407122104743\n4700.0,single_0_children,0.0005411144634079858\n4700.0,couple_0_children,0.0026680308495920175\n4700.0,"couple_2_children",0.001120084367220105\n4800.0,single_0_children,0.0004891754168899605\n4800.0,couple_0_children,0.0024956525382356714\n4800.0,"couple_2_children",0.0010551354266130487\n4900.0,single_0_children,0.00044261857534192057\n4900.0,couple_0_children,0.0023343015284003556\n4900.0,"couple_2_children",0.0009936709160497021\n5000.0,single_0_children,0.00040084696327485333\n5000.0,couple_0_children,0.0021833446753841508\n5000.0,"couple_2_children",0.000935560135830357\n5100.0,single_0_children,0.00036333385599116513\n5100.0,couple_0_children,0.0020421699339329977\n5100.0,"couple_2_children",0.0008806673448218603\n5200.0,single_0_children,0.0003296140924895612\n5200.0,couple_0_children,0.001910188780878459\n5200.0,"couple_2_children",0.0008288539803205317\n5300.0,single_0_children,0.0002992765044577906\n5300.0,couple_0_children,0.0017868378362831119\n5300.0,"couple_2_children",0.000779980479617249\n5400.0,single_0_children,0.0002719573145947343\n5400.0,couple_0_children,0.0016715798378803325\n5400.0,"couple_2_children",0.0007339077610416597\n5500.0,single_0_children,0.00024733437680471405\n5500.0,couple_0_children,0.0015639040979773845\n5500.0,"couple_2_children",0.000690498415003551\n5600.0,single_0_children,0.0002251221476744382\n5600.0,couple_0_children,0.0014633265502400432\n5600.0,"couple_2_children",0.0006496176490219033\n5700.0,single_0_children,0.0002050672933470962\n5700.0,couple_0_children,0.0013693894753762975\n5700.0,"couple_2_children",0.0006111340249019009\n5800.0,single_0_children,0.00018694484868711058\n5800.0,couple_0_children,0.0012816609792080094\n5800.0,"couple_2_children",0.000574920021050666\n5900.0,single_0_children,0.00017055485672439144\n5900.0,couple_0_children,0.0011997342835527655\n5900.0,"couple_2_children",0.0005408524483599905\n6000.0,single_0_children,0.00015571942597970408\n6000.0,couple_0_children,0.0011232268793726916\n6000.0,"couple_2_children",0.0005088127440801578\n6100.0,single_0_children,0.00014228015159799043\n6100.0,couple_0_children,0.001051779582465647\n6100.0,"couple_2_children",0.0004786871646045972\n6200.0,single_0_children,0.00013009585342167325\n6200.0,couple_0_children,0.0009850555243075937\n6200.0,"couple_2_children",0.00045036689503408277\n6300.0,single_0_children,0.00011904059036076177\n6300.0,couple_0_children,0.0009227391042708023\n6300.0,"couple_2_children",0.0004237480907374\n6400.0,single_0_children,0.00010900191581103703\n6400.0,couple_0_children,0.0008645349241373276\n6400.0,"couple_2_children",0.0003987318638290222\n6500.0,single_0_children,9.987934352141459e-05\n6500.0,couple_0_children,0.000810166721435122\n6500.0,"couple_2_children",0.00037522422550143427\n6600.0,single_0_children,9.158299734521087e-05\n6600.0,couple_0_children,0.0007593763144966386\n6600.0,"couple_2_children",0.00035313599344087256\n6700.0,single_0_children,8.40324217888555e-05\n6700.0,couple_0_children,0.0007119225691547194\n6700.0,"couple_2_children",0.00033238267208608003\n6800.0,single_0_children,7.715553328787624e-05\n6800.0,couple_0_children,0.0006675803945425539\n6800.0,"couple_2_children",0.0003128843122302905\n6900.0,single_0_children,7.088769474535237e-05\n6900.0,couple_0_children,0.0006261397734681907\n6900.0,"couple_2_children",0.00029456535538875596\n7000.0,single_0_children,6.517089812937744e-05\n7000.0,couple_0_children,0.0005874048312101966\n7000.0,"couple_2_children",0.0002773544674333479\n7100.0,single_0_children,5.995304187716468e-05\n7100.0,couple_0_children,0.0005511929452701373\n7100.0,"couple_2_children",0.00026118436521203875\n7200.0,single_0_children,5.5187291554991526e-05\n7200.0,couple_0_children,0.0005173338975664687\n7200.0,"couple_2_children",0.0002459916392047188\n7300.0,single_0_children,5.0831513689223775e-05\n7300.0,couple_0_children,0.0004856690697177329\n7300.0,"couple_2_children",0.0002317165747011121\n7400.0,single_0_children,4.684777396137374e-05\n7400.0,couple_0_children,0.0004560506814014721\n7400.0,"couple_2_children",0.0002183029735091809\n7500.0,single_0_children,4.3201892070309524e-05\n7500.0,couple_0_children,0.000428341071264839\n7500.0,"couple_2_children",0.00020569797779881484\n7600.0,single_0_children,3.986304652614642e-05\n7600.0,couple_0_children,0.0004024120194670544\n7600.0,"couple_2_children",0.00019385189734645207\n7700.0,single_0_children,3.680342347840795e-05\n7700.0,couple_0_children,0.0003781441106399085\n7700.0,"couple_2_children",0.00018271804116211848\n7800.0,single_0_children,3.399790441268884e-05\n7800.0,couple_0_children,0.0003554261358379309\n7800.0,"couple_2_children",0.00017225255424270034\n7900.0,single_0_children,3.142378818307059e-05\n7900.0,couple_0_children,0.00033415453189895996\n7900.0,"couple_2_children",0.00016241425999739785\n8000.0,single_0_children,2.9060543402052745e-05\n8000.0,couple_0_children,0.00031423285653868195\n8000.0,"couple_2_children",0.00015316450872807154\n8100.0,single_0_children,2.6889587694272573e-05\n8100.0,couple_0_children,0.00029557129744676514\n8100.0,"couple_2_children",0.00014446703241178193\n8200.0,single_0_children,2.4894090741080485e-05\n8200.0,couple_0_children,0.00027808621363072735\n8200.0,"couple_2_children",0.00013628780592255104\n8300.0,single_0_children,2.3058798412154595e-05\n8300.0,couple_0_children,0.0002616997072549988\n8300.0,"couple_2_children",0.00012859491473978326\n8400.0,single_0_children,2.1369875602745388e-05\n8400.0,couple_0_children,0.00024633922425000874\n8400.0,"couple_2_children",0.00012135842911800547\n8500.0,single_0_children,1.9814765678505652e-05\n8500.0,couple_0_children,0.0002319371820032622\n8500.0,"couple_2_children",0.00011455028463504887\n8600.0,single_0_children,1.8382064675439244e-05\n8600.0,couple_0_children,0.00021843062249614993\n8600.0,"couple_2_children",0.00010814416899097817\n8700.0,single_0_children,1.7061408621552398e-05\n8700.0,couple_0_children,0.00020576088931014441\n8700.0,"couple_2_children",0.00010211541489380584\n8800.0,single_0_children,1.5843372533984418e-05\n8800.0,couple_0_children,0.00019387332699209806\n8800.0,"couple_2_children",9.644089884297895e-05\n8900.0,single_0_children,1.4719379816478691e-05\n8900.0,couple_0_children,0.00018271700133469464\n8900.0,"couple_2_children",9.109894560118057e-05\n9000.0,single_0_children,1.3681620925833243e-05\n9000.0,couple_0_children,0.00017224443920327588\n9000.0,"couple_2_children",8.606923813233687e-05\n9100.0,single_0_children,1.2722980305555694e-05\n9100.0,couple_0_children,0.00016241138660823547\n9100.0,"couple_2_children",8.133273277481462e-05\n9200.0,single_0_children,1.1836970700221419e-05\n9200.0,couple_0_children,0.0001531765837968775\n9200.0,"couple_2_children",7.68715794142463e-05\n9300.0,single_0_children,1.1017674063319023e-05\n9300.0,couple_0_children,0.0001445015562062546\n9300.0,"couple_2_children",7.26690464190921e-05\n9400.0,single_0_children,1.0259688358795697e-05\n9400.0,couple_0_children,0.00013635042019032642\n9400.0,"couple_2_children",6.870945010362735e-05\n9500.0,single_0_children,9.558079635560006e-06\n9500.0,couple_0_children,0.00012868970249780334\n9500.0,"couple_2_children",6.497808848548523e-05\n9600.0,single_0_children,8.908338823962826e-06\n9600.0,couple_0_children,0.00012148817254477789\n9600.0,"couple_2_children",6.146117911082346e-05\n9700.0,single_0_children,8.306342761063769e-06\n9700.0,couple_0_children,0.00011471668658424912\n9700.0,"couple_2_children",5.814580072579486e-05\n9800.0,single_0_children,7.748319008558582e-06\n9800.0,couple_0_children,0.00010834804293580353\n9800.0,"couple_2_children",5.5019838579678485e-05\n9900.0,single_0_children,7.230814073053024e-06\n9900.0,couple_0_children,0.0001023568474916975\n9900.0,"couple_2_children",5.2071933154022413e-05\n10000.0,single_0_children,6.750664681364526e-06\n10000.0,couple_0_children,9.671938877141043e-05\n10000.0,"couple_2_children",4.92914321188757e-05\n',
    ),
)

## Erstellen des DataFrames für die Analyse

Stapeln der DataFrames mit unterschiedlichen Haushaltstypen. Aufsummieren der
Bruttoeinkommen. Dann Zusammenfügen mit Gewichten.

In [ ]:
df = pd.concat((_df_1e_0k, _df_2e_0k, _df_2e_2k))
_bruttolohn_m_hh = (
    df.groupby("hh_id")["bruttolohn_m"]
    .sum()
    .to_frame()
    .rename(columns={"bruttolohn_m": "bruttolohn_m_hh"})
)
df = df.join(_bruttolohn_m_hh, on="hh_id")
df = pd.merge(left=df.reset_index(), right=_gewichte, how="inner")
df

## Ausrechnen der Steuern und Transfers mit GETTSIM 

In [ ]:
_ergebnisse_personen_vor_reform = compute_taxes_and_transfers(
    data=df,
    functions=policy_func_dict,
    params=params_dict,
    targets=[
        "sozialv_beitr_m",
        "arbeitsl_geld_2_m_hh",
        "kindergeld_m_hh",
        "wohngeld_m_hh",
        "kinderzuschl_m_hh",
        "eink_st_tu",
        "soli_st_tu",
    ],
)
# hh_id und bruttolohn_m dem DataFrame hinzufügen.
_ergebnisse_personen_vor_reform = _ergebnisse_personen_vor_reform.join(
    df[["hh_id", "bruttolohn_m"]],
)
_ergebnisse_personen_vor_reform

In [ ]:
# Zahlen auf Haushaltsebene aggregieren.
ergebnisse_vor_reform = _ergebnisse_personen_vor_reform.groupby("hh_id").agg(
    {
        "bruttolohn_m": lambda x: x.sum(),
        "kindergeld_m_hh": lambda x: x.max(),
        "eink_st_tu": lambda x: x.max() / 12,
        "soli_st_tu": lambda x: x.max() / 12,
        "sozialv_beitr_m": lambda x: x.sum(),
        "arbeitsl_geld_2_m_hh": lambda x: x.max(),
        "wohngeld_m_hh": lambda x: x.max(),
        "kinderzuschl_m_hh": lambda x: x.max(),
    },
)
# Reformzeitpunkt
ergebnisse_vor_reform["zeitpunkt"] = "Vor Reform"
# Haushaltstyp und Gewichte anspielen.
ergebnisse_vor_reform = ergebnisse_vor_reform.join(
    df[["hh_id", "hh_typ", "gewicht"]].drop_duplicates().set_index("hh_id"),
)
ergebnisse_vor_reform = ergebnisse_vor_reform.reset_index().set_index(
    ["zeitpunkt", "hh_typ", "hh_id"],
)
ergebnisse_vor_reform

# Aufgabe 1: Analyse des Status quo (gesamt: 30 Punkte)

# Aufgabe 1.1: Einkommensteuerlast

## Aufgabe 1.1.1 (5 Punkte)

Plotten Sie die Einkommensteuerlast (ohne Soli) für jeden Haushaltstyp und geben Sie der Graphik eine passende Überschrift.

## Aufgabe 1.1.2 (6 Punkte)

Erläutern Sie die Unterschiede zwischen den drei Linien!

# Aufgabe 1.2: Transfers

## Aufgabe 1.2.1 (5 Punkte)

Summieren Sie Arbeitslosengeld 2, Wohngeld, Kinderzuschlag und Kindergeld in einer Variable "transfers_m_hh" auf, plotten Sie diese und geben Sie der Graphik eine passende Überschrift.

## Aufgabe 1.2.2 (6 Punkte)

Erläutern Sie die Unterschiede zwischen den drei Linien! Bitte konzentrieren Sie sich auf die großen Unterschiede, Details wie sich auf kurzen Abschnitten ändernde Steigungen können Sie ignorieren.

# Aufgabe 1.3: Verfügbares Einkommen 

## Aufgabe 1.3.1 (4 Punkte)

Berechnen Sie das verfügbare Einkommen für jeden Haushalt.

**Bitte benennen Sie die Spalte "`verfügbares_einkommen`", wir werden sie später verwenden.**

## Aufgabe 1.3.2 (4 Punkte)

Plotten Sie das verfügbare Einkommmen für alle drei Haushaltstypen in der selben Graphik und geben Sie der Graphik eine passende Überschrift.

# Aufgabe 2: Stufentarif für die Einkommensteuer (gesamt: 40 Punkte)

Eine erste Reform, die wir betrachten wollen, ist eine Vereinfachung des
Einkommensteuertarifs. Sie hat zwei Komponenten:

1. Der neue Einkommensteuertarif hat lediglich zwei Stufen des Grenzsteuersatzes. Er
   soll die derzeitige Einkommensteuer **und den Solidaritätszuschlag** ersetzen.
2. Der Kinderfreibetrag wird auf 600 Euro pro Monat und Kind erhöht. Die Aufteilung in
   sächliches Existenzminimum und Beiträge für Erziehung und Ausbildung ist dabei
   irrelevant.

Diese Reform dient vor allem der Vorbereitung von Aufgaben 3 und 4, ist aber auch von
eigenem Interesse.

## Implementierung der Reform und Ausrechnen der Steuern und Transfers

Der Code in der folgenden Zelle definiert die verschiedenen Steuerfreibeträge sowie die
beiden Einkommensintervalle mit positiven Grenzsteuersätzen.

In [ ]:
freibetrag = 14400
knoten = 35000
satz_1 = 0.3
satz_2 = 0.45

params_dict_steuerreform = deepcopy(params_dict)
params_dict_steuerreform["eink_st"]["eink_st_tarif"] = {
    "thresholds": np.array([-np.inf, freibetrag, knoten, np.inf]),
    "rates": np.array([[0, satz_1, satz_2]]),
    "intercepts_at_lower_thresholds": np.array([0, 0, (knoten - freibetrag) * satz_1]),
}
params_dict_steuerreform["eink_st_abzuege"]["kinderfreib"] = {
    "beitr_erz_ausb": 0,
    "sächl_existenzmin": 7200,
}

In [ ]:
_ergebnisse_personen_nach_steuerreform = compute_taxes_and_transfers(
    data=df,
    functions=policy_func_dict,
    params=params_dict_steuerreform,
    targets=[
        "kindergeld_m_hh",
        "sozialv_beitr_m",
        "arbeitsl_geld_2_m_hh",
        "kindergeld_m_tu",
        "wohngeld_m_hh",
        "kinderzuschl_m_hh",
        "eink_st_tu",
    ],
)
# Mithilfe der p_id wieder die hh_id und den bruttolohn an das DataFrame joinen
_ergebnisse_personen_nach_steuerreform = _ergebnisse_personen_nach_steuerreform.join(
    df[["hh_id", "bruttolohn_m"]],
)
# Zahlen auf Haushaltsebene aggregieren.
ergebnisse_nach_steuerreform = _ergebnisse_personen_nach_steuerreform.groupby(
    "hh_id",
).agg(
    {
        "bruttolohn_m": lambda x: x.sum(),
        "kindergeld_m_hh": lambda x: x.max(),
        "eink_st_tu": lambda x: x.max() / 12,
        "sozialv_beitr_m": lambda x: x.sum(),
        "arbeitsl_geld_2_m_hh": lambda x: x.max(),
        "wohngeld_m_hh": lambda x: x.max(),
        "kinderzuschl_m_hh": lambda x: x.max(),
    },
)

# Reformzeitpunkt
ergebnisse_nach_steuerreform["zeitpunkt"] = "Stufentarif + Kinderfreibetrag"
# Haushaltstyp anspielen.
ergebnisse_nach_steuerreform = ergebnisse_nach_steuerreform.join(
    df[["hh_id", "hh_typ", "gewicht"]].drop_duplicates().set_index("hh_id"),
)
ergebnisse_nach_steuerreform = ergebnisse_nach_steuerreform.reset_index().set_index(
    ["zeitpunkt", "hh_typ", "hh_id"],
)
ergebnisse_nach_steuerreform

# Aufgabe 2.1: Verfügbares Einkommen


## Aufgabe 2.1.1 (5 Punkte)

Berechnen Sie das verfügbare Einkommen für jeden Haushalt. Achtung: Die Berechnung ist nicht identisch zu Aufgabe 1.1.3. 

## Aufgabe 2.1.2 (5 Punkte)

Plotten Sie das verfügbare Einkommmen für alle drei Haushaltstypen in der selben Graphik und geben Sie der Graphik eine passende Überschrift.

# Aufgabe 2.2: Differenz in den verfügbaren Einkommen und Grenzbelastungen

In dieser Aufgabe sind Plots der verfügbaren Einkommen nach Haushaltstyp vorgegeben.
Jede der drei Graphiken vergleicht die Situation vor und nach der Steuerreform. 

Führen Sie die Zellen aus und interpretieren Sie die Unterschiede, wie in Aufgabe 2.2.1 angegeben.

## Zusammenfügen der Outputvariablen vor und nach der Reform

In [ ]:
vergleich_1 = pd.concat((ergebnisse_vor_reform, ergebnisse_nach_steuerreform))
vergleich_1

In [ ]:
range_y = (0, 7500)

vergleich_1.reset_index().plot.line(
    x="bruttolohn_m",
    y="verfügbares_einkommen",
    color="zeitpunkt",
    title="Verfügbares Einkommen",
    facet_col="hh_typ",
    range_y=range_y,
).update_layout(legend={"orientation": "h", "y": -0.3, "xanchor": "center", "x": 0.5})

## Aufgabe 2.2.1 (12 Punkte)

Interpretieren Sie die Unterschiede zwischen den Linien jenseits von 5.000 Euro in den
drei Graphen. 

NB: Falls erwünscht, können Sie sich die Werte der veränderten Parameter vor der Reform wie folgt ansehen:

```python
params_dict["eink_st"]['eink_st_tarif']
params_dict["soli_st"]
params_dict["eink_st_abzuege"]['kinderfreib']
```

## Aufgabe 2.2.2 (6 Punkte)

Die folgende Zelle definiert eine Funktion, welche die gesamte Grenzbelastung ausrechnet.

Anschließend wird diese Funktion aufgerufen, um die gesamte Grenzbelastung dem DataFrame `vergleich` hinzuzufügen.

Erstellen Sie in den darauffolgenden Zellen eine Graphik für die gesamte Grenzbelastung
analog zu der Graphik für verfügbares Einkommen in der Einleitung zu Aufgabe 2.2. Das
heißt:

- Jede der drei Untergraphiken soll die die Situation vor und nach der Steuerreform für
  einen Haushaltstyp vergleichen.
- Die y-Achse soll bei allen drei Untergraphiken das Interval `[-0,05; 1,05]` sein.


In [ ]:
def grenzbelastung_gesamt(vgl):
    """Gesamte Grenzbelastung auf Basis des verfügbaren Einkommens berechnen."""
    grenzb = (
        vgl["verfügbares_einkommen"]
        - vgl.groupby(["zeitpunkt", "hh_typ"])["verfügbares_einkommen"].shift(-1)
    ) / 100 + 1
    return grenzb


vergleich_1["grenzbelastung_gesamt"] = grenzbelastung_gesamt(vgl=vergleich_1)

# Aufgabe 2.2.3: Interpretation der Grenzbelastungen (12 Punkte)

Vergleichen Sie die Grenzbelastungen innerhalb der drei Haushaltstypen. Konzentrieren
Sie sich dabei auf die drei folgenden Fragen:

1. In welchem Bereich sind die Grenzbelastungen identisch?
2. Warum sind die Grenzbelastungen jenseits von 5.000 Euro vor der Reform
   abschnittsweise ansteigend, danach jedoch abschnittsweise flach?
3. Halten Sie die Unterschiede für wesentlich in dem Sinne, dass Sie (auf einem
freigewählten Abschnitt von etwa 1000 Euro, in dem Unterschiede bestehen) ein anderes
Arbeitsangebot erwarten? Begründen Sie Ihre Antwort und geben Sie jeweils mindestens ein
pro- und ein contra-Argument.

# Aufgabe 3: Pilotprojekt Grundeinkommen (gesamt: 35 Punkte)

Das Pilotprojekt Grundeinkommen (https://www.pilotprojekt-grundeinkommen.de) hat
regelmäßig mediale Aufmerksamkeit bekommen. Das Projekt hat 122 Personen jeden Monat
zusätzlich 1.200 Euro gezahlt. In dieser Aufgabe wollen wir die Effekte simulieren.

Dazu einige Punkte:
- Wir gehen vom Basisszenario **nach** der Steuerreform in Aufgabe 2 aus; der Grund
  dafür wird unten in Aufgabe 4 klar.
- Wir gehen davon aus, dass das Grundeinkommen wie ein Lottogewinn behandelt wird:
  Anrechnung auf Transfers (Arbeitslosengeld 2, Wohngeld, Kinderzuschlag), es werden
  allerdings keine Steuern fällig.
- Wir gehen davon aus, dass eine Person pro Haushalt teilnehmen darf
- In GETTSIM existiert ein Konstrukt *Sonstiges Einkommen* (`sonstig_eink_m`), welches
  diese Eigenschaften hat. Wir müssen nur die Daten entsprechend anpassen und geben
  derjenigen Person im Haushalt, die ohnehin ein Einkommen erzielt, auch dieses dazu.

In [ ]:
df_bge_pilot = df.copy()
idx = df_bge_pilot.query("bruttolohn_m > 0").index
df_bge_pilot.loc[idx, "sonstig_eink_m"] = 1200
# Beim jeweils ersten Haushalt pro Gruppe wird keinerlei Lohn erzielt, daher greift die
# vorige Bedingung nicht und wir bessern manuell nach.
idx = df_bge_pilot[df_bge_pilot["hh_typ"] != df_bge_pilot["hh_typ"].shift(1)].index
df_bge_pilot.loc[idx, "sonstig_eink_m"] = 1200

In [ ]:
params_dict_steuerreform = deepcopy(params_dict)
params_dict_steuerreform["eink_st"]["eink_st_tarif"] = {
    "thresholds": np.array([-np.inf, 14400.0, 35000, np.inf]),
    "rates": np.array([[0, 0.3, 0.45]]),
    "intercepts_at_lower_thresholds": np.array([0, 0, (35000 - 14400) * 0.3]),
}
params_dict_steuerreform["eink_st_abzuege"]["kinderfreib"] = {
    "beitr_erz_ausb": 0,
    "sächl_existenzmin": 7200,
}


_ergebnisse_personen_nach_bge_pilot = compute_taxes_and_transfers(
    data=df_bge_pilot,
    functions=policy_func_dict,
    params=params_dict_steuerreform,
    targets=[
        "kindergeld_m_hh",
        "sozialv_beitr_m",
        "arbeitsl_geld_2_m_hh",
        "kindergeld_m_tu",
        "wohngeld_m_hh",
        "kinderzuschl_m_hh",
        "eink_st_tu",
    ],
)
# Mithilfe der p_id wieder die hh_id, bruttolohn etc. an das DataFrame joinen
_ergebnisse_personen_nach_bge_pilot = _ergebnisse_personen_nach_bge_pilot.join(
    df_bge_pilot[["hh_id", "bruttolohn_m", "sonstig_eink_m"]],
)
# Zahlen auf Haushaltsebene aggregieren.
ergebnisse_nach_bge_pilot = _ergebnisse_personen_nach_bge_pilot.groupby("hh_id").agg(
    {
        "bruttolohn_m": lambda x: x.sum(),
        "sonstig_eink_m": lambda x: x.sum(),
        "kindergeld_m_hh": lambda x: x.max(),
        "eink_st_tu": lambda x: x.max() / 12,
        "sozialv_beitr_m": lambda x: x.sum(),
        "arbeitsl_geld_2_m_hh": lambda x: x.max(),
        "wohngeld_m_hh": lambda x: x.max(),
        "kinderzuschl_m_hh": lambda x: x.max(),
    },
)

# Reformzeitpunkt
ergebnisse_nach_bge_pilot["zeitpunkt"] = "BGE Pilot"
# Haushaltstyp anspielen.
ergebnisse_nach_bge_pilot = ergebnisse_nach_bge_pilot.join(
    df[["hh_id", "hh_typ", "gewicht"]].drop_duplicates().set_index("hh_id"),
    ## solution
)
ergebnisse_nach_bge_pilot = ergebnisse_nach_bge_pilot.reset_index().set_index(
    ["zeitpunkt", "hh_typ", "hh_id"],
)
ergebnisse_nach_bge_pilot

## Aufgabe 3.1: Verfügbares Einkommen (5 Punkte)

Berechnen Sie das verfügbare Einkommen für Gewinner des Pilotprojekts Grundeinkommen aus. Achtung: Die Berechnung ist nicht identisch zu Aufgabe 1.1.3. oder 2.1.1.

## Vergleich ist nun zwischen Stufentarif und BGE Pilot

In [ ]:
vergleich_2 = pd.concat((ergebnisse_nach_steuerreform, ergebnisse_nach_bge_pilot))
vergleich_2

## Aufgabe 3.2 Plots des verfügbaren Einkommens (6 Punkte)

Erstellen Sie eine Graphik für den Vergleich des verfügbaren Einkommens zwischen der
Situation nach der Steuerreform sowie für Gewinner des Pilotprojekts Grundeinkommen
(unter der Annahme, sie befänden sich auch in der Situation nach der Steuerreform)
analog zu den Graphiken in der Einleitung zu Aufgabe 2.2. Das heißt:

- Jede der drei Untergraphiken soll die verfügbaren Einkommen für einen Haushaltstyp
  über verschiedene Situationen hinweg vergleichen.
- Die y-Achse soll bei allen drei Graphiken gleich sein und ein vernünftiges Intervall
  abdecken

# Aufgabe 3.3 Plots der Grenzbelastungen (8 Punkte)

Erstellen Sie drei Graphiken für die gesamte Grenzbelastung analog zu den Graphiken
für verfügbares Einkommen in der Einleitung zu Aufgabe 2.2. Das heißt:

- Jede der drei Graphiken soll die die Situation vor und nach der Steuerreform für einen Haushaltstyp vergleichen.
- Die Überschriften sollen sauber und aussagekräftig seinm
- Die y-Achse soll bei allen drei Graphiken das Interval `[-0,05; 1,05]` sein.

Zur Berechnung der Grenzbelastung können Sie die Funktion von oben wiederverwenden.

# Aufgabe 3.4: Effekte des Pilotprojekts Grundeinkommens auf Einkommen und Steuern (8 Punkte)

Vergleichen Sie die verfügbaren Einkommen und Grenzbelastungen für die einzelnen
Haushaltstypen. Wo sehen Sie Unterschiede und warum? Verlieren Sie sich nicht in
Details.

Falls Sie zwischen 400 und 500 Euro Bruttoeinkommen einen Sprung in der Grenzbelastung
beim BGE Piloten sehen, ignorieren Sie diesen. Er liegt daran, dass das Steuer- und
Sozialversicherungssystem so nicht mehr auf Minijobs eingestellt ist und tritt beim
tatsächlich gültigen System nicht in der Schärfe auf. Das zu ändern hätte zu große
Eingriffe erfordert.

# Aufgabe 3.5: Bewertung des Pilotprojekts Grundeinkommen (8 Punkte)

Was erwarten Sie für das Arbeitsangebot einzelner Gruppen? Argumentieren Sie ökonomisch. Weitere Hinweise: 
- Ignorieren Sie mögliche Effekte von Arbeitsunterbrechungen auf spätere Möglichkeiten, Einkommen zu erzielen. 
- Ignorieren Sie Konsumglättung über die Zeit (es werden keinerlei Ersparnisse gebildet)
- Denken Sie jedoch an den Grenznutzen des Konsums. 

# Aufgabe 4: Bedingungsloses Grundeinkommen (gesamt 40 Punkte)

In dieser Aufgabe gehen wir von einer Möglichkeit aus, ein bedingungsloses Grundeinkommen einzuführen.
- Jede(r) Erwachsene erhält 1200 Euro, jedes Kind 600 Euro
- Das bedingungslose Grundeinkommen ersetzt alle Transfers mit Bedürftigkeitsprüfung und das Kindergeld, nicht jedoch die Sozialversicherungen, deren Beiträge bleiben bestehen.
- In GETTSIM codieren wir die Leistungen des Grundeinkommens als "Einkünfte aus Vermietung und Verpachtung": Diese sind einkommensteuerpflichtig.
- Wir gehen wieder vom Reformszenario mit den Stufentarifen aus. Die Werte für Grund- und Kinderfreibetrag in der Reform oben waren so gewählt, dass die Zahlungen aus dem Grundeinkommen für alle Haushalte steuerfrei sind. D.h., Steuerzahlungen setzen für alle Haushalte grundsätzlich mit dem ersten verdienten Euro ein.

In [ ]:
df_bge = df.copy()
idx = df_bge.query("alter >= 18").index
df_bge.loc[idx, "vermiet_eink_m"] = 1200
# Für Kinder erhöhen wir die Beträge von Erwachsenen
idx = df_bge.query("alter >= 18 & hh_typ == 'couple_2_children'").index
df_bge.loc[idx, "vermiet_eink_m"] += 600

In [ ]:
params_dict_bge = deepcopy(params_dict_steuerreform)
for n in params_dict_bge["kindergeld"]["kindergeld"]:
    params_dict_bge["kindergeld"]["kindergeld"][n] = 0

_ergebnisse_personen_nach_bge = compute_taxes_and_transfers(
    data=df_bge,
    functions=policy_func_dict,
    params=params_dict_bge,
    targets=[
        "sozialv_beitr_m",
        "eink_st_tu",
    ],
)
# Mithilfe der p_id wieder die hh_id, bruttolohn etc. an das DataFrame joinen
_ergebnisse_personen_nach_bge = _ergebnisse_personen_nach_bge.join(
    df_bge[["hh_id", "bruttolohn_m", "vermiet_eink_m"]],
)
# Zahlen auf Haushaltsebene aggregieren.
ergebnisse_nach_bge = _ergebnisse_personen_nach_bge.groupby("hh_id").agg(
    {
        "bruttolohn_m": lambda x: x.sum(),
        "vermiet_eink_m": lambda x: x.sum(),
        "eink_st_tu": lambda x: x.max() / 12,
        "sozialv_beitr_m": lambda x: x.sum(),
    },
)

# Reformzeitpunkt
ergebnisse_nach_bge["zeitpunkt"] = "BGE"
# Haushaltstyp anspielen.
ergebnisse_nach_bge = ergebnisse_nach_bge.join(
    df[["hh_id", "hh_typ", "gewicht"]].drop_duplicates().set_index("hh_id"),
)
ergebnisse_nach_bge = ergebnisse_nach_bge.reset_index().set_index(
    ["zeitpunkt", "hh_typ", "hh_id"],
)
ergebnisse_nach_bge

## Aufgabe 4.1: Verfügbares Einkommen (4 Punkte)

Berechnen Sie das verfügbare Einkommen für Gewinner des Pilotprojekts Grundeinkommen aus. Achtung: Die Berechnung ist nicht identisch zu Aufgabe 1.1.3., 2.1.1. oder 3.1.

## BGE zum vorhergehenden Vergleich hinzufügen

In [ ]:
vergleich_3 = pd.concat((vergleich_2, ergebnisse_nach_bge))
vergleich_3

## Aufgabe 4.2 Plots von verfügbarem Einkommen und Grenzsteuersätzen (6 Punkte)

Erstellen Sie Graphiken für den Vergleich des verfügbaren Einkommens sowie der Grenzsteuersätze für die drei im DataFrame `vergleich_3` enthaltenen Situationen:

- Nach der Steuerreform
- Für Gewinner des Pilotprojekts Grundeinkommen (unter der Annahme, sie befänden sich auch in der Situation nach
der Steuerreform) 
- Für die Situation nach Steuerreform und Einführung eines BGE

Insgesamt sind also 6 Graphiken zu erstellen. Hinweise:

- Jede der Graphiken soll die drei Situationen für einen Haushaltstyp vergleichen.
- Die Überschriften sollen sauber und aussagekräftig sein
- Die y-Achse soll über die jeweils drei Graphiken für verfügbares Einkommen / Grenzbelastungen hinweg gleich sein und ein vernünftiges Intervall abdecken (bei Grenzbelastungen bitte das gleiche Intervall wie oben wählen)


# Aufgabe 4.3: Effekte des bedingungslosen Grundeinkommens auf Einkommen und Steuern (6 Punkte)

Vergleichen Sie die verfügbaren Einkommen und Grenzbelastungen für die einzelnen Haushaltstypen. Wo sehen Sie Unterschiede und warum? Verlieren Sie sich nicht in Details.

Falls Sie zwischen 400 und 500 Euro Bruttoeinkommen einen Sprung in der Grenzbelastung sehen, ignorieren Sie diesen. Er liegt daran, dass das Steuer- und Sozialversicherungssystem so nicht mehr auf Minijobs eingestellt ist, das zu ändern, hätte zu große Eingriffe erfordert.

# Aufgabe 4.4: Effekt des bedingungslosen Grundeinkommens auf Einnahmen / Ausgaben des Staates

Je nach Haushaltseinkommen können wir die Bilanz des Staates ausrechnen, d.h., emfpängt ein Haushalt netto finanzielle Transfers oder zahlt er netto an den Staat? Hierzu rechnen wir die Differenz zwischen dem Bruttolohn und dem verfügbaren Einkommen aus.

Wir ignorieren das Pilotprojekt Grundeinkommen, da es die Finanzierungsseite explizit ausblendet.

In [ ]:
vergleich_bge = vergleich_3.query(
    "zeitpunkt in ['Stufentarif + Kinderfreibetrag', 'BGE']",
).copy()
vergleich_bge["staatsbilanz"] = (
    vergleich_bge["bruttolohn_m"] - vergleich_bge["verfügbares_einkommen"]
)
vergleich_bge

## Aufgabe 4.4.1 (5 Punkte)

Plotten Sie die Variable `staatsbilanz` gegen das verfügbare Einkommen, analog zu den Graphiken
für verfügbares Einkommen in der Einleitung zu Aufgabe 2.2. Das heißt:

- Jede der drei Graphiken soll die beiden Situationen für einen Haushaltstyp vergleichen.
- Die Überschriften sollen sauber und aussagekräftig sein
- Die y-Achse soll bei allen drei Graphiken gleich sein und ein sinnvolles Intervall abdecken



## Aufgabe 4.4.2 (6 Punkte)

Interpretieren Sie die Graphiken! Gehen Sie insbesondere auf die Unterschiede zwischen den Haushaltstypen ein. 

## Aufgabe 4.4.3 (8 Punkte)

Die Spalte `gewicht` enthält von der Einkommensverteilung im Mikrozensus inspirierete Gewichte für Haushalte nach Typ und Bruttoeinkommen. Sie für einen DataFrame auf Haushaltsebene normalisiert auf 1.

Wir können die Nettoeinkünfte des Staates pro Kopf ausrechnen, indem wir die Staatsbilanz damit multiplizieren und dann aufsummieren.

In [ ]:
vergleich_bge["staatsbilanz_gewichtet"] = (
    vergleich_bge["staatsbilanz"] * vergleich_bge["gewicht"]
)
vergleich_bge["staatsbilanz_gewichtet"].groupby("zeitpunkt").sum().to_frame().round(0)

Wie Sie sehen und wenig überraschend ergibt sich ein hoher Fehlbetrag. Wie weit können
Sie diesen Fehlbetrag herunterdrehen, indem Sie nur den Grenzsteuersatz für Personen mit
Einkünften über 35000 Euro anpassen? Der Grenzsteuersatz sollte 1 nicht überschreiten.

Wir wiederholen die Parameter der Steuerreform, damit sie diese leicht anpassen können.

In [ ]:
freibetrag = 14400
knoten = 35000
satz_1 = 0.3
satz_2 = 0.45

Setzen Sie hier Ihren Code ein., um den Grenzsteuersatz anzupassen.

In [ ]:
params_dict_bge_balance = deepcopy(params_dict_bge)
params_dict_bge_balance["eink_st"]["eink_st_tarif"] = {
    "thresholds": np.array([-np.inf, freibetrag, knoten, np.inf]),
    "rates": np.array([[0, satz_1, satz_2]]),
    "intercepts_at_lower_thresholds": np.array([0, 0, (knoten - freibetrag) * satz_1]),
}

_ergebnisse_personen_nach_bge_balance = compute_taxes_and_transfers(
    data=df_bge,
    functions=policy_func_dict,
    params=params_dict_bge_balance,
    targets=[
        "sozialv_beitr_m",
        "eink_st_tu",
    ],
)

**Führen Sie nun folgende Aufgaben aus:**

- Aggregieren Sie die relevanten Zahlen auf Haushaltsebene
- Fügen Sie den Haushaltstyp und das Gewicht hinzu
- Rechnen Sie das verfügbare Einkommen aus
- Rechnen Sie die Staatsbilanz pro Kopf aus

## Aufgabe 4.4.4 (5 Punkte)

Interpretieren Sie Ihr Ergebnis!

# Aufgabe 5 (5 Punkte)

*(aus Ihren Vorschlägen in Woche 4)*

Warum würden Hochverdiener von einer Senkung der Steuer für Geringverdiener profitieren?